# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [A2C]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 399, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 399 (delta 0), reused 2 (delta 0), pack-reused 393
Receiving objects: 100% (399/399), 151.25 MiB | 21.48 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from stable_baselines3 import A2C #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')
wandb, version 0.13.4


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7fd380cc6250>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21943.19 , over-consume=kWh  39465.2 , under-consume=kWh  17522.0 , Total_cost=€  898.15 , overcost=€  1395.45 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/A2C_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/A2C_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/A2C_VPP_simulator.ipynb"


In [21]:
#Loading training model, from local directory or from wandb previous trainings
A2C_path = "trained_models/A2C_models/model_A2C_"

model_id = "1u6pwi97"
model = A2C.load(A2C_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21208.35 , over-consume=kWh  38317.46 , under-consume=kWh  17109.11 , Total_cost=€  883.84 , overcost=€  1377.81 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6202.97 , over-consume=KWh  7078.91 , under-consume=KWh  13281.88 , Total_cost=€  -91.14 , Overcost=€  256.89 
 EV_INFO: Av.EV_energy_leaving=kWh  64.79 , Std.EV_energy_leaving=kWh  33.76 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 143114.2 - Step_rewars (load_t= 176729.58, EVs_energy_t= -30244.47)
 - Final_rewards (EVs_energy= 13591.26, Overconsume= -6724.23, Underconsume= -10805.71, Overcost= 567.78)
Episode:1 Score:143114.1986632583


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  36.028385  43.664886  42.963772  59.634422   
2022-01-01 00:15:00  36.278385  43.085880  42.384766  59.884422   
2022-01-01 00:30:00  36.528385  42.502392  41.801277  60.134422   
2022-01-01 00:45:00  36.778385  42.024277  41.323162  60.384422   
2022-01-01 01:00:00  37.028385  41.597584  40.896469  60.634422   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  99.989998  19.925613  29.807667  78.060387   
2022-06-06 05:00:00  99.989998  19.925613  29.557667  79.740242   
2022-06-06 05:15:00  99.989998  19.925613  29.307667  81.289467   
2022-06-06 05:30:00  99.989998  19.925613  29.057667  82.930176   
2022-06-06 05:45:00  99.989998  19.925613  28.807667  84.494881   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [3127, 3129, 3128, 3126]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [3127, 3129, 3128, 3126]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [3127, 3129, 3128, 3126]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [3127, 3129, 3128, 3126]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [3578, 3579, 3580, 3581]  [1, 2, 2, 1]   
2022-06-06 05:00:00  [3578, 3579, 3580, 3581]  [1, 2, 2, 1]   
2022-06-06 05:15:00  [3578, 3579, 3580, 3581]  [1, 2, 2, 1]   
2022-06-06 05:30:00  [3578, 3579, 3580, 3581]  [1, 2, 2, 1]   
2022-06-06 05:45:00  [3578, 3579, 3580, 3581]  [1, 2, 2, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, True, False]        2.000000   
2022-01-01 00:30:00    [False, True, True, False]        2.000000   
2022-01-01 00:45:00    [False, True, True, False]        2.000000   
2022-01-01 01:00:00    [False, True, True, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00   [False, False, False, True]        5.130472   
2022-06-06 05:00:00   [False, False, False, True]        6.719441   
2022-06-06 05:15:00   [False, False, False, True]        6.196898   
2022-06-06 05:30:00   [False, False, False, True]        6.562833   
2022-06-06 05:45:00   [False, False, False, True]        6.258828   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.485647e+00    15.000000        0.0   
2022-01-01 00:15:00          -4.632052  0.000000e+00    15.000000        0.0   
2022-01-01 00:30:00          -4.667893 -4.440892e-16    15.000000        0.0   
2022-01-01 00:45:00          -3.824905  2.220446e-16    15.000000        0.0   
2022-01-01 01:00:00          -3.413555  0.000000e+00    15.000000        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000 -5.130455e+00    -7.472204        0.0   
2022-06-06 05:00:00          -1.000000 -6.719424e+00    -6.997165        0.0   
2022-06-06 05:15:00          -1.000000 -6.196881e+00    -7.329833        0.0   
2022-06-06 05:30:00          -1.000000 -6.562816e+00    -7.053465        0.0   
2022-06-06 05:45:00          -1.000000 -6.258811e+00    -7.404084        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  -7.472204  
2022-06-06 05:00:00  -6.997165  
2022-06-06 05:15:00  -7.329833  
2022-06-06 05:30:00  -7.053465  
20

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 07:45:00, Parking_time: 23.59592187716961, Leaving_time: 2022-01-02 07:20:45.318758, SOC: 0.5026175575809809, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 16:30:00, Parking_time: 23.334600374330552, Leaving_time: 2023-01-01 15:50:04.561348, SOC: 0.5250394725565017, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12541.71 , over-consume=kWh  33665.81 , under-consume=kWh  21124.1 , Total_cost=€  609.92 , overcost=€  1468.18 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = A2C.load(A2C_path + model_id, env=env)

In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12881.25 , over-consume=kWh  34256.19 , under-consume=kWh  21374.94 , Total_cost=€  613.01 , overcost=€  1483.53 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -13266.84 , over-consume=KWh  3257.43 , under-consume=KWh  16524.27 , Total_cost=€  -502.65 , Overcost=€  150.27 
 EV_INFO: Av.EV_energy_leaving=kWh  66.19 , Std.EV_energy_leaving=kWh  33.04 , EV_departures =  1040 , EV_queue_left =  0
SCORE:  Cumulative_reward= 162949.5 - Step_rewars (load_t= 190182.27, EVs_energy_t= -25380.64)
 - Final_rewards (EVs_energy= 10964.24, Overconsume= -3064.91, Underconsume= -10745.01, Overcost= 993.54)
Episode:1 Score:162949.50101436186


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0    1          2          3  \
time                                                        
2022-01-01 00:00:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:15:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:30:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:45:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 01:00:00   0.000000  0.0   0.000000   0.000000   
...                        ...  ...        ...        ...   
2022-06-06 04:45:00  85.040947  0.0  35.216152  75.590836   
2022-06-06 05:00:00  86.894043  0.0  34.966152  77.443932   
2022-06-06 05:15:00  88.889534  0.0  34.716152  79.439423   
2022-06-06 05:30:00  90.687546  0.0  34.466152  81.237434   
2022-06-06 05:45:00  92.626205  0.0  34.216152  83.176094   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
...                                    ...           ...   
2022-06-06 04:45:00  [6677, 0, 6675, 6676]  [1, 2, 2, 1]   
2022-06-06 05:00:00  [6677, 0, 6675, 6676]  [1, 2, 2, 1]   
2022-06-06 05:15:00  [6677, 0, 6675, 6676]  [1, 2, 2, 1]   
2022-06-06 05:30:00  [6677, 0, 6675, 6676]  [1, 2, 2, 1]   
2022-06-06 05:45:00  [6677, 0, 6675, 6676]  [1, 2, 2, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00    [True, True, False, True]        0.000000   
2022-01-01 00:15:00    [True, True, False, True]        0.000000   
2022-01-01 00:30:00    [True, True, False, True]        0.000000   
2022-01-01 00:45:00    [True, True, False, True]        0.000000   
2022-01-01 01:00:00    [True, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00   [True, False, False, True]       11.110372   
2022-06-06 05:00:00   [True, False, False, True]       14.824787   
2022-06-06 05:15:00   [True, False, False, True]       15.963953   
2022-06-06 05:30:00   [True, False, False, True]       14.384102   
2022-06-06 05:45:00  [False, False, False, True]       15.509303   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.740427    -5.089158        0.0   
2022-01-01 00:15:00                0.0 -4.098073    -5.062419        0.0   
2022-01-01 00:30:00                0.0 -4.068661    -3.657693        0.0   
2022-01-01 00:45:00                0.0 -3.194616    -4.316828        0.0   
2022-01-01 01:00:00                0.0 -3.590097    -4.907821        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:00:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00               -1.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.089158  
2022-01-01 00:15:00  -5.062419  
2022-01-01 00:30:00  -3.657693  
2022-01-01 00:45:00  -4.316828  
2022-01-01 01:00:00  -4.907821  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:45:00  15.000000  

[15000 rows x 13 columns]

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 12:15:00, Parking_time: 24, Leaving_time: 2022-01-02 12:15:00, SOC: 0.32389344171281115, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 12:00:00, Parking_time: 23.616981075853374, Leaving_time: 2023-01-01 11:37:01.131873, SOC: 0.6486981404429827, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8153.63 , over-consume=kWh  31843.41 , under-consume=kWh  23689.79 , Total_cost=€  456.84 , overcost=€  1324.15 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = A2C.load(A2C_path + model_id, env=env)

In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8300.91 , over-consume=kWh  32187.93 , under-consume=kWh  23887.02 , Total_cost=€  496.36 , overcost=€  1365.79 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -17009.04 , over-consume=KWh  2384.66 , under-consume=KWh  19393.71 , Total_cost=€  -584.29 , Overcost=€  104.1 
 EV_INFO: Av.EV_energy_leaving=kWh  67.22 , Std.EV_energy_leaving=kWh  32.75 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 162085.18 - Step_rewars (load_t= 183572.81, EVs_energy_t= -23467.1)
 - Final_rewards (EVs_energy= 10142.28, Overconsume= -2207.58, Underconsume= -11473.0, Overcost= 5517.76)
Episode:1 Score:162085.1766346174


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0          1          2    3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:15:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:30:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:45:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 01:00:00   0.000000   0.000000   0.000000  0.0   
...                        ...        ...        ...  ...   
2022-06-06 03:30:00  99.989998  26.349667  34.739964  0.0   
2022-06-06 03:45:00  99.989998  26.099667  34.489964  0.0   
2022-06-06 04:00:00  99.989998  25.849667  34.239964  0.0   
2022-06-06 04:15:00  99.989998  25.599667  33.989964  0.0   
2022-06-06 04:30:00  99.989998  25.349667  33.739964  0.0   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [0, 0, 1, 0]   
...                                    ...           ...   
2022-06-06 03:30:00  [9810, 9812, 9811, 0]  [1, 2, 2, 2]   
2022-06-06 03:45:00  [9810, 9812, 9811, 0]  [1, 2, 2, 2]   
2022-06-06 04:00:00  [9810, 9812, 9811, 0]  [1, 2, 2, 2]   
2022-06-06 04:15:00  [9810, 9812, 9811, 0]  [1, 2, 2, 2]   
2022-06-06 04:30:00  [9810, 9812, 9811, 0]  [1, 2, 2, 2]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00     [True, True, False, True]        0.000000   
2022-01-01 00:15:00     [True, True, False, True]        0.000000   
2022-01-01 00:30:00     [True, True, False, True]        0.000000   
2022-01-01 00:45:00     [True, True, False, True]        0.000000   
2022-01-01 01:00:00     [True, True, False, True]        0.000000   
...                                           ...             ...   
2022-06-06 03:30:00  [False, False, False, False]        0.000009   
2022-06-06 03:45:00  [False, False, False, False]        0.000009   
2022-06-06 04:00:00  [False, False, False, False]        0.000009   
2022-06-06 04:15:00  [False, False, False, False]        0.000009   
2022-06-06 04:30:00  [False, False, False, False]        0.000009   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.727645    -4.794587        0.0   
2022-01-01 00:15:00                0.0 -3.876752    -5.186870        0.0   
2022-01-01 00:30:00                0.0 -4.205557    -3.942510        0.0   
2022-01-01 00:45:00                0.0 -3.365506    -6.542390        0.0   
2022-01-01 01:00:00                0.0 -5.696630    -5.985474        0.0   
...                                ...       ...          ...        ...   
2022-06-06 03:30:00               -2.0 -6.498049    -6.946901        0.0   
2022-06-06 03:45:00               -2.0 -6.141591    -9.781072        0.0   
2022-06-06 04:00:00               -2.0 -9.259179    -9.697125        0.0   
2022-06-06 04:15:00               -2.0 -9.166837   -10.313144        0.0   
2022-06-06 04:30:00               -2.0 -9.844458    -8.708325       50.1   

                       rewards  
time                            
2022-01-01 00:00:00  -4.794587  
2022-01-01 00:15:00  -5.186870  
2022-01-01 00:30:00  -3.942510  
2022-01-01 00:45:00  -6.542390  
2022-01-01 01:00:00  -5.985474  
...                        ...  
2022-06-06 03:30:00  -6.946901  
2022-06-06 03:45:00  -9.781072  
2022-06-06 04:00:00  -9.697125  
2022-06-06 04:15:00 -10.313144  
2022-06-06 04:30:00  41.391675  

[14995 rows x 13 columns]

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

In [63]:
#env.close()